## 8. Evaluating Prompts

Before the advent of large-language models, machine-learning systems were trained using a technique called [supervised learning](https://en.wikipedia.org/wiki/Supervised_learning). This approach required users to provide carefully prepared training data that showed the computer what was expected.

For instance, if you were developing a model to distinguish spam emails from legitimate ones, you would need to provide the model with a set of spam emails and another set of legitimate emails. The model would then use that data to learn the relationships between the inputs and outputs, which it could then apply to new emails.

In addition to training the model, the curated input would be used to evaluate the model's performance. This process typically involved splitting the supervised data into two sets: one for training and one for testing. The model could then be evaluated using a separate set of supervised data to ensure it could generalize beyond the examples it had been fed during training.

Large-language models operate differently. They are trained on vast amounts of text and can generate responses based on the relationships they derive from various machine-learning approaches. The result is that they can be used to perform a wide range of tasks without requiring supervised data to be prepared beforehand.

This is a significant advantage. However, it also raises questions about evaluating an LLM prompt. If we don't have a supervised sample to test its results, how do we know if it's doing a good job? How can we improve its performance if we can't see where it gets things wrong?

In the final chapters, we will show how traditional supervision can still play a vital role in evaluating and improving an LLM prompt.

In [84]:
import time # NEW
import json
from rich import print
from rich.progress import track # NEW
import requests
from retry import retry
import pandas as pd
from huggingface_hub import InferenceClient

api_key = os.getenv("HF_TOKEN")
client = InferenceClient(
    token=api_key,
)
df = pd.read_csv("https://raw.githubusercontent.com/palewire/first-llm-classifier/refs/heads/main/_notebooks/Form460ScheduleESubItem.csv")

Start by outputting a random sample from the dataset to a file of comma-separated values. It will serve as our supervised sample. In general, the larger the sample the better the evaluation. But at a certain point the returns diminish. For this exercise, we will use a sample of 250 records.

In [85]:
df.sample(250).to_csv("./sample.csv", index=False)

You can open the file in a spreadsheet program like Excel or Google Sheets. For each payee in the sample, you would provide the correct category in a companion column. This gradually becomes the supervised sample.

![Sample](https://palewi.re/docs/first-llm-classifier/_images/sample.png)

To speed the class along, we've already prepared a sample for you in [the class repository](https://github.com/palewire/first-llm-classifier). Our next step is to read it back into a DataFrame.

In [86]:
sample_df = pd.read_csv("sample_classified.csv")

We'll install the Python packages `scikit-learn`, `matplotlib`, and `seaborn`. Prior to LLMs, these libraries were the go-to tools for training and evaluating machine-learning models. We'll primarily be using them for testing.

Return to the Jupyter notebook and install the packages alongside our other dependencies.

In [ ]:
%pip install huggingface_hub rich ipywidgets retry pandas scikit-learn matplotlib seaborn

Add the `test_train_split` function from `scikit-learn` to the import statement.

In [88]:
import json
from rich import print
import requests
from retry import retry
import pandas as pd
from sklearn.model_selection import train_test_split #NEW 

This tool is used to split a supervised sample into separate sets for training and testing.

The first input is the DataFrame column containing our supervised payees. The second input is the DataFrame column containing the correct categories.

The `test_size` parameter determines the proportion of the sample that will be used for testing. The `random_state` parameter ensures that the split is reproducible by setting a seed for the random number generator that draws the samples.

In [89]:
training_input, test_input, training_output, test_output = train_test_split(
    sample_df[['payee']],
    sample_df['category'],
    test_size=0.33,
    random_state=42, # Remember Jackie Robinson. Remember Douglas Adams.
)

In a traditional training setup, the next step would be to train a machine-learning model in `sklearn` using the `training_input` and `training_output` sets. The model would then be evaluated using the `test_input` and `test_output` sets.

With the LLM we skip ahead to the testing phase. We pass the `test_input` set to our LLM prompt and compare the results to the right answers found in `test_output` set.

All that requires is that we pass the `payee` column from our `test_input` DataFrame to the function we created in the previous chapters.

In [90]:
###REPEAT FROM PREVIOUS NOTEBOOK
@retry(ValueError, tries=2, delay=2)
def classify_payees(name_list):
    prompt = """You are an AI model trained to categorize businesses based on their names.

You will be given a list of business names, each separated by a new line.

Your task is to analyze each name and classify it into one of the following categories: Restaurant, Bar, Hotel, or Other.

It is extremely critical that there is a corresponding category output for each business name provided as an input.

If a business does not clearly fall into Restaurant, Bar, or Hotel categories, you should classify it as "Other".

Even if the type of business is not immediately clear from the name, it is essential that you provide your best guess based on the information available to you. If you can't make a good guess, classify it as Other.

For example, if given the following input:

"Intercontinental Hotel\nPizza Hut\nCheers\nWelsh's Family Restaurant\nKTLA\nDirect Mailing"

Your output should be a JSON list in the following format:

["Hotel", "Restaurant", "Bar", "Restaurant", "Other", "Other"]

This means that you have classified "Intercontinental Hotel" as a Hotel, "Pizza Hut" as a Restaurant, "Cheers" as a Bar, "Welsh's Family Restaurant" as a Restaurant, and both "KTLA" and "Direct Mailing" as Other.

Ensure that the number of classifications in your output matches the number of business names in the input. It is very important that the length of JSON list you return is exactly the same as the number of business names you receive.
"""
    response = client.chat.completions.create(
        messages=[
            {
                "role": "system",
                "content": prompt,
            },
            {
                "role": "user",
                "content": "Intercontinental Hotel\nPizza Hut\nCheers\nWelsh's Family Restaurant\nKTLA\nDirect Mailing",
            },
            {
                "role": "assistant",
                "content": '["Hotel", "Restaurant", "Bar", "Restaurant", "Other", "Other"]',
            },
            {
                "role": "user",
                "content": "Subway Sandwiches\nRuth Chris Steakhouse\nPolitical Consulting Co\nThe Lamb's Club",
            },
            {
                "role": "assistant",
                "content": '["Restaurant", "Restaurant", "Other", "Bar"]',
            },
            {
                "role": "user",
                "content": "\n".join(name_list),
            }
        ],
        model="meta-llama/Llama-3.3-70B-Instruct",
        temperature=0,
    )

    answer_str = response.choices[0].message.content
    answer_list = json.loads(answer_str)

    acceptable_answers = [
        "Restaurant",
        "Bar",
        "Hotel",
        "Other",
    ]
    for answer in answer_list:
        if answer not in acceptable_answers:
            raise ValueError(f"{answer} not in list of acceptable answers")

    try:
        assert len(name_list) == len(answer_list)
    except AssertionError:
        raise ValueError(f"Number of outputs ({len(name_list)}) does not equal the number of inputs ({len(answer_list)})")

    return dict(zip(name_list, answer_list))

def get_batch_list(li, n=10):
    """Split the provided list into batches of size `n`."""
    batch_list = []
    for i in range(0, len(li), n):
        batch_list.append(li[i : i + n])
    return batch_list
    
def classify_batches(name_list, batch_size=11, wait=2):
    """Split the provided list of names into batches and classify with our LLM them one by one."""
    # Create a place to store the results
    all_results = {}

    # Batch up the list
    batch_list = get_batch_list(name_list, n=batch_size)

    # Loop through the list in batches
    for batch in track(batch_list):
        # Classify it with the LLM
        batch_results = classify_payees(batch)

        # Add what we get back to the results
        all_results.update(batch_results)

        # Tap the brakes to avoid overloading HF's API
        time.sleep(wait)

    # Return the results
    return all_results
    
llm_dict = classify_batches(list(test_input.payee))

Output()

Next, we import the `classification_report` and `confusion_matrix` functions from `sklearn`, which are used to evaluate a model's performance. We'll also pull in `seaborn` and `matplotlib` to visualize the results.

In [91]:
import json
from rich import print
import requests
from retry import retry
import pandas as pd
import seaborn as sns # NEW
import matplotlib.pyplot as plt # NEW 
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report # NEW

The `classification_report` function generats a report card on a model's performance. You provide it with the correct answers in the `test_output` set and the model's predictions in your prompt's DataFrame. In this case, our LLM's predictions are stored in the `llm_df` DataFrame's `category` column.

In [92]:
llm_df = pd.DataFrame.from_dict(llm_dict, orient="index", columns=["category"])

In [93]:
print(classification_report(test_output, llm_df.category))

precision    recall  f1-score   support

         Bar       1.00      1.00      1.00         2
       Hotel       1.00      1.00      1.00         9
       Other       1.00      0.98      0.99        57
  Restaurant       0.94      1.00      0.97        15

    accuracy                           0.99        83
   macro avg       0.98      1.00      0.99        83
weighted avg       0.99      0.99      0.99        83

That will output a report that looks something like this:

```
              precision    recall  f1-score   support

         Bar       1.00      1.00      1.00         2
       Hotel       0.89      0.80      0.84        10
       Other       0.96      0.96      0.96        57
  Restaurant       0.87      0.93      0.90        14

    accuracy                           0.94        83
   macro avg       0.93      0.92      0.93        83
weighted avg       0.94      0.94      0.94        83
```

At first, the report can be a bit overwhelming. What are all these technical terms?

Precision measures what statistics nerds call "positive predictive value." It's how often the model made the correct decision when it applied a category. For instance, in the "Bar" category, the LLM correctly predicted both of the bars in our supervised sample. That's a precision of 1.00. An analogy here is a baseball player's contact rate. Precision is a measure of how often the model connects with the ball when it swings its bat.

Recall measures how many of the supervised instances were identified by the model. In this case, it shows that the LLM correctly spotted 80% of the hotels in our manual sample.

The f1-score is a combination of precision and recall. It's a way to measure a model's overall performance by balancing the two.

The support column shows how many instances of each category were in the supervised sample.

The averages at the bottom combine the results for all categories. The macro row is a simple average all the scores in that column. The weighted row is a weighted average based on the number of instances in each category.

In the example result provided above, we can see that the LLM was guessing correctly more than 90% of the time no matter how you slice it.

Another technique for evaluating classifiers is to visualize the results using a chart known as a confusion matrix. This chart shows how often the model correctly predicted each category and where it got things wrong.

Drawing one up requires the `confusion_matrix` function from `sklearn` and an embarassing tangle of code from `seaborn` and `matplotlib` libraries. Most of it is boilerplate, but you need to punch your test variables, as well as the proper labels for the categories, in a few picky places.

In [ ]:
conf_mat = confusion_matrix(
    test_output, # labels
    llm_df.category, # labels
    labels=llm_df.category.unique() # labels
)
fig, ax = plt.subplots(figsize=(5,5))
sns.heatmap(
    conf_mat,
    annot=True,
    fmt='d',
    xticklabels=llm_df.category.unique(), # labels
    yticklabels=llm_df.category.unique() # labels
)
plt.ylabel('Actual')
plt.xlabel('Predicted')

![confusion matrix](https://palewi.re/docs/first-llm-classifier/_images/matrix-llm.png)

The diagonal line of cells running from the upper left to the lower right shows where the model correctly predicted the category. The off-diagonal cells show where it got things wrong. The color of the cells indicates how often the model made that prediction. For instance, we can see that one miscategorized hotel in the sample was predicted to be a restaurant and the second was predicted to be "Other."

Due to the inherent randomness in the LLM's predictions, it's a good idea to test your sample and run these reports multiple times to get a sense of the model's performance.

Before we look at how you might improve the LLM's performance, let's take a moment to compare the results of this evaluation against the old school approach where the supervised sample is used to train a machine-learning model that doesn't have access to the ocean of knowledge poured into an LLM.

This will require importing a mess of `sklearn` functions and classes. We'll use `TfidfVectorizer` to convert the payee text into a numerical representation that can be used by a `LinearSVC` classifier. We'll then use a `Pipeline` to chain the two together. If you have no idea what any of that means, don't worry. Now that we have LLMs in this world, you might never need to know.

In [ ]:
import json
from rich import print
import requests
from retry import retry
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report
from sklearn.svm import LinearSVC # NEW
from sklearn.pipeline import Pipeline # NEW
from sklearn.compose import ColumnTransformer # NEW
from sklearn.feature_extraction.text import TfidfVectorizer # NEW

Here's a simple example of how you might train and evaluate a traditional machine-learning model using the supervised sample.

First you setup all the machinery.

In [ ]:
vectorizer = TfidfVectorizer(
    sublinear_tf=True,
    min_df=5,
    norm='l2',
    encoding='latin-1',
    ngram_range=(1, 3),
)
preprocessor = ColumnTransformer(
    transformers=[
        ('payee', vectorizer, 'payee')
    ],
    sparse_threshold=0,
    remainder='drop'
)
pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('classifier', LinearSVC(dual="auto"))
])

Then you train the model using those training sets we split out at the start.

In [ ]:
model = pipeline.fit(training_input, training_output)

And you ask the model to use its training to predict the right answers for the test set.

In [ ]:
predictions = model.predict(test_input)

Now, you can run the same evaluation code as before to see how the traditional model performed.

In [ ]:
print(classification_report(test_output, predictions))

```
              precision    recall  f1-score   support

         Bar       0.00      0.00      0.00         2
       Hotel       1.00      0.27      0.43        10
       Other       0.75      1.00      0.85        57
  Restaurant       0.80      0.29      0.42        14

    accuracy                           0.76        83
   macro avg       0.64      0.39      0.43        83
weighted avg       0.77      0.76      0.70        83
```

In [ ]:
conf_mat = confusion_matrix(test_output, llm_df.category, labels=llm_df.category.unique())
fig, ax = plt.subplots(figsize=(5,5))
sns.heatmap(
    conf_mat,
    annot=True,
    fmt='d',
    xticklabels=llm_df.category.unique(),
    yticklabels=llm_df.category.unique()
)
plt.ylabel('Actual')
plt.xlabel('Predicted')

![confusion matrix](https://palewi.re/docs/first-llm-classifier/_images/matrix-ml.png)

Not great. The traditional model is guessing correctly about 75% of the time, but it's missing most cases of our "Bar", "Hotel" and "Restaurant" categories as almost everything is getting filed as "Other." The LLM, on the other hand, is guessing correctly more than 90% of the time and flagging many of the rare categories that we're seeking to find in the haystack of data.

**[9. Improving prompts →](ch9-improving-prompts.ipynb)**